In [1]:
%matplotlib inline

In [43]:
from __future__ import division

import sys
import time
import logging

import numpy as np
from scipy.io import loadmat
from os import path

# change this to the path of mushu if you don't have it in your
# PYTHONPATH already
sys.path.append('../../mushu')
sys.path.append('../')

import libmushu
from libmushu.driver.replayamp import ReplayAmp
from wyrm.types import RingBuffer
import wyrm.processing as proc
from wyrm import io
from wyrm.types import Data, BlockBuffer, RingBuffer

#Classifiers
from sklearn.svm import SVC, LinearSVC
from sklearn.calibration import CalibratedClassifierCV
from sklearn.preprocessing import scale, MinMaxScaler
from sklearn import metrics
import matplotlib
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import pickle
from sklearn.externals import joblib
from os import listdir
from os.path import isfile, join

In [2]:
logging.basicConfig(format='%(relativeCreated)10.0f %(threadName)-10s %(name)-10s %(levelname)8s %(message)s', level=logging.NOTSET)
logger = logging.getLogger(__name__)

In [11]:
# replay the experiment in real time?
REALTIME = False


TRAIN_DATA_A = '../BCI_Comp_III_Wads_2004/data/Subject_A_Train.mat'
TEST_DATA_A = '../BCI_Comp_III_Wads_2004/data/Subject_A_Test.mat'

TRAIN_DATA_B = '../BCI_Comp_III_Wads_2004/data/Subject_B_Train.mat'
TEST_DATA_B = '../BCI_Comp_III_Wads_2004/data/Subject_B_Test.mat'

CHANNEL_DATA = '../BCI_Comp_III_Wads_2004/data/eloc64.txt'

TRUE_LABELS_TEST = "WQXPLZCOMRKO97YFZDEZ1DPI9NNVGRQDJCUVRMEUOOOJD2UFYPOO6J7LDGYEGOA5VHNEHBTXOO1TDOILUEE5BFAEEXAW_K4R3MRU"

STIMULUS_CODE = {
    # cols from left to right
    1 : "agmsy5",
    2 : "bhntz6",
    3 : "ciou17",
    4 : "djpv28",
    5 : "ekqw39",
    6 : "flrx4_",
    # rows from top to bottom
    7 : "abcdef",
    8 : "ghijkl",
    9 : "mnopqr",
    10: "stuvwx",
    11: "yz1234",
    12: "56789_"
}
MATRIX = ['abcdef',
          'ghijkl',
          'mnopqr',
          'stuvwx',
          'yz1234',
          '56789_']

MARKER_DEF_TRAIN = {'target': ['target'], 'nontarget': ['nontarget']}
MARKER_DEF_TEST = {i : [i] for i in STIMULUS_CODE.values()}

SEG_IVAL = [0, 800]

In [12]:
def load_bci_TESTdata(filename):
    """Load the BCI Competition III Data Set 2.
    This method loads the data set and converts it into Wyrm's ``Data``
    format. Before you use it, you have to download the data set in
    Matlab format and unpack it. The directory with the extracted files
    must contain the ``Subject_*.mat``- and the ``eloc64.txt`` files.
    .. note::
        If you need the true labels of the test sets, you'll have to
        download them separately from
        http://bbci.de/competition/iii/results/index.html#labels
    Parameters
    ----------
    filename : str
        The path to the matlab file to load
    Returns
    -------
    cnt : continuous `Data` object
    Examples
    --------
    >>> dat = load_bcicomp3_ds2('/home/foo/data/Subject_A_Train.mat')
    """
    STIMULUS_CODE = {
        0 : "blankMatrix",
        # cols from left to right
        1 : "agmsy5",
        2 : "bhntz6",
        3 : "ciou17",
        4 : "djpv28",
        5 : "ekqw39",
        6 : "flrx4_",
        # rows from top to bottom
        7 : "abcdef",
        8 : "ghijkl",
        9 : "mnopqr",
        10: "stuvwx",
        11: "yz1234",
        12: "56789_"
        }

    # load the matlab data
    data_mat = loadmat(filename)
    # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filename), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2
    # The signal is recorded with 64 channels, bandpass filtered
    # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
    # Samples x Channels
    data = data_mat['Signal'][60:,:,:]
    data = data.astype('double')
#     print('data: ',data.shape)
    # For each sample: 1 if a row/colum was flashed, 0 otherwise
    flashing = data_mat['Flashing'][60:,:]
    flashing = flashing.reshape(-1)
#     print('flashing: ',flashing.shape)
    #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
    ##Creates an array where only the initial intensifications of each series appear
    tmp = []
    for i, _ in enumerate(flashing):
        if i == 0:
            tmp.append(flashing[i])
            continue
        if flashing[i] == flashing[i-1] == 1:
            tmp.append(0)
            continue
        tmp.append(flashing[i])
    flashing = np.array(tmp)
    # For each sample: 0 when no row/colum was intensified,
    # 1..6 for intensified columns, 7..12 for intensified rows
    stimulus_code = data_mat['StimulusCode'][60:,:].reshape(-1)
#     print('stim_code: ', stimulus_code.shape)
    stimulus_code = stimulus_code[flashing == 1]
    # 0 if no row/col was intensified or the intensified did not contain
    # the target character, 1 otherwise
    stimulus_type = data_mat.get('StimulusType', np.array([]))[60:,:].reshape(-1)
#     print('stim_type: ', stimulus_type.shape)
    # The target characters
    target_chars = data_mat.get('TargetChar')[0][60:]
#     target_chars = data_mat.get('TargetChar', np.array([])).reshape(-1)
    fs = 240
    data = data.reshape(-1, 64)
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    #stimulus_code = zip([t for t, _ in flashing], [STIMULUS_CODE[i] for i in stimulus_code])
    #Raises error "TypeError: '<' not supported between instances of 'tuple' and 'list'" when calling sort() 
    #stimulus_code =[[t for t,_ in flashing], [STIMULUS_CODE[i] for i in stimulus_code]]
    #print(type(stimulus_code), type(flashing), type(targets), type(nontargets))
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
    return dat


In [13]:
def load_bci_TRAINdata(filename):
    """Load the BCI Competition III Data Set 2.
    This method loads the data set and converts it into Wyrm's ``Data``
    format. Before you use it, you have to download the data set in
    Matlab format and unpack it. The directory with the extracted files
    must contain the ``Subject_*.mat``- and the ``eloc64.txt`` files.
    .. note::
        If you need the true labels of the test sets, you'll have to
        download them separately from
        http://bbci.de/competition/iii/results/index.html#labels
    Parameters
    ----------
    filename : str
        The path to the matlab file to load
    Returns
    -------
    cnt : continuous `Data` object
    Examples
    --------
    >>> dat = load_bcicomp3_ds2('/home/foo/data/Subject_A_Train.mat')
    """
    STIMULUS_CODE = {
        0 : "blankMatrix",
        # cols from left to right
        1 : "agmsy5",
        2 : "bhntz6",
        3 : "ciou17",
        4 : "djpv28",
        5 : "ekqw39",
        6 : "flrx4_",
        # rows from top to bottom
        7 : "abcdef",
        8 : "ghijkl",
        9 : "mnopqr",
        10: "stuvwx",
        11: "yz1234",
        12: "56789_"
        }

    # load the matlab data
    data_mat = loadmat(filename)
    # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filename), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2
    # The signal is recorded with 64 channels, bandpass filtered
    # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
    # Samples x Channels
    data = data_mat['Signal'][:60,:,:]
    data = data.astype('double')
#     print('data: ',data.shape)
    # For each sample: 1 if a row/colum was flashed, 0 otherwise
    flashing = data_mat['Flashing'][:60,:]
    flashing = flashing.reshape(-1)
#     print('flashing: ',flashing.shape)
    #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
    ##Creates an array where only the initial intensifications of each series appear
    tmp = []
    for i, _ in enumerate(flashing):
        if i == 0:
            tmp.append(flashing[i])
            continue
        if flashing[i] == flashing[i-1] == 1:
            tmp.append(0)
            continue
        tmp.append(flashing[i])
    flashing = np.array(tmp)
    # For each sample: 0 when no row/colum was intensified,
    # 1..6 for intensified columns, 7..12 for intensified rows
    stimulus_code = data_mat['StimulusCode'][:60,:].reshape(-1)
#     print('stim_code: ', stimulus_code.shape)
    stimulus_code = stimulus_code[flashing == 1]
    # 0 if no row/col was intensified or the intensified did not contain
    # the target character, 1 otherwise
    stimulus_type = data_mat.get('StimulusType', np.array([]))[:60,:].reshape(-1)
#     print('stim_type: ', stimulus_type.shape)
    # The target characters
    target_chars = data_mat.get('TargetChar')[0][:60]
#     target_chars = data_mat.get('TargetChar', np.array([])).reshape(-1)
    
    fs = 240
    data = data.reshape(-1, 64)
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    #stimulus_code = zip([t for t, _ in flashing], [STIMULUS_CODE[i] for i in stimulus_code])
    #Raises error "TypeError: '<' not supported between instances of 'tuple' and 'list'" when calling sort() 
    #stimulus_code =[[t for t,_ in flashing], [STIMULUS_CODE[i] for i in stimulus_code]]
    #print(type(stimulus_code), type(flashing), type(targets), type(nontargets))
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
    return dat


In [14]:
def train(filename):
    cnt = load_bci_TRAINdata(filename)

    fs_n = cnt.fs / 2

    b, a = proc.signal.butter(5, [10 / fs_n], btype='low')
    cnt = proc.lfilter(cnt, b, a)

#     b, a = proc.signal.butter(5, [.4 / fs_n], btype='high')
#     cnt = proc.lfilter(cnt, b, a)

    cnt = proc.subsample(cnt, 20)

    epo = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL)

    #from wyrm import plot
    #plot.plot_spatio_temporal_r2_values(proc.sort_channels(epo))
    #print JUMPING_MEANS_IVALS
    #plot.plt.show()

    fv = proc.create_feature_vectors(epo)
    X = scale(fv.data)
    y = fv.axes[0]
#     X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size = 0.3, train_size = 0.7)

    #     clf = proc.lda_train(fv)
    clf = CalibratedClassifierCV(base_estimator=LinearSVC(C = 1, class_weight = 'balanced'), cv=2)
    clf.fit(X,y)
    return clf

In [69]:
def online_experiment(amp, cfy, scaler, subject, C):
    amp_fs = amp.get_sampling_frequency()
    amp_channels = amp.get_channels()
    C = str(C)
    file = open('sim_training_LinearSVM_C='+C+'_'+subject+'.txt', 'w')
    file.write('LinearSVM C='+C+'Online simulation, subject '+subject)
    
    # csv results file
    filename = 'results/'+subject+'/Results_LinearSVM_C='+C+'_'+subject+'.csv'
    columnNames = 'Character,Trial,Correct/12,isCorrect_ch_pred,recall_acum,precision_acum,accuracy'

    resultsFile = open(filename, 'w')
    resultsFile.write(columnNames)    
    
    chfilename = 'results/'+subject+'/CharacterResults_LinearSVM_C='+C+'_'+subject+'.csv'
    chcolumnNames = 'Character,Trial 1,Trial 2,Trial 3,Trial 4,Trial 5, Trial 6,\
    Trial 7,Trial 8,Trial 9,Trial 10,Trial 11,Trial 12,Trial 13,Trial 14,Trial 15,Trial 16'
    chResultsFile = open(chfilename, 'w')
    chResultsFile.write(chcolumnNames)     

    #buf = BlockBuffer(4)
    rb = RingBuffer(5000)

    fn = amp_fs / 2
    b_low, a_low = proc.signal.butter(5, [10 / fn], btype='low')
#     b_high, a_high = proc.signal.butter(5, [.4 / fn], btype='high')

    zi_low = proc.lfilter_zi(b_low, a_low, len(amp_channels))
#     zi_high = proc.lfilter_zi(b_high, a_high, len(amp_channels))

    amp.start()
    markers_processed = 0
#     current_letter_idx = 0
#     current_letter = TRUE_LABELS[current_letter_idx].lower()

    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
    endresult = []
    file.write('\nCharacter #'+str(len(endresult)+1))

   # t0 = time.time()
    #data, markers = amp.get_data()
    
    y_true = np.array([])
    y_pred = np.array([])
    
    correct_letter = False #boolean to know if the letter has already been predicted
    
    while True:
        t0 = time.time()

        # get fresh data from the amp
        data, markers = amp.get_data()
        if len(data) == 0:
            continue

        # we should rather wait for a specific end-of-experiment marker
        if len(data) == 0:
            break

        # convert to cnt
        cnt = io.convert_mushu_data(data, markers, amp_fs, amp_channels)
        
        ## enter the block buffer
        #buf.append(cnt)
        #cnt = buf.get()
        #if not cnt:
        #    continue

        # low-pass and subsample
        cnt, zi_low = proc.lfilter(cnt, b_low, a_low, zi=zi_low)
#         cnt, zi_high = proc.lfilter(cnt, b_high, a_high, zi=zi_high)

        cnt = proc.subsample(cnt, 20)

        newsamples = cnt.data.shape[0]

        # enter the ringbuffer
        rb.append(cnt)
        cnt = rb.get()

        # segment
        epo = proc.segment_dat(cnt, MARKER_DEF_TEST, SEG_IVAL, newsamples=newsamples)
        epo_train = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL, newsamples=newsamples)
        if not epo: # If not enough data for 800 ms
            continue

        fv = proc.create_feature_vectors(epo)
        fv_train = proc.create_feature_vectors(epo_train)
        
        logger.debug('Markers processed: ')
        logger.debug(markers_processed)
        
        
        clf_out = cfy.predict_proba(scaler.transform(fv.data))[:,1] #Estimate probabilities
        y_true = np.append(y_true, fv_train.axes[0])
        
        y_pred_now = cfy.predict(scaler.transform(fv.data))  #Predict classes
        y_pred = np.append(y_pred, y_pred_now)
        
        y_correct = y_pred_now == fv_train.axes[0]
        print('Predicho: ', fv_train.axes[0],'\tVerdadero: ', y_pred_now, y_correct )

#         clf_out = proc.lda_apply(fv, cfy)
        markers = [fv.class_names[cls_idx] for cls_idx in fv.axes[0]]
        result = zip(markers, clf_out)
        
        report = metrics.classification_report(y_true, y_pred)
        recall = metrics.recall_score(y_true, y_pred)
        precision = metrics.precision_score(y_true, y_pred)
        accuracy = metrics.accuracy_score(y_true, y_pred)
        f1 = metrics.f1_score(y_true, y_pred)
        print('\nP300 classification metrics...')
        print('recall: ', recall, '\tprecision: ', precision, '\tf1: ', f1, '\taccuracy: ', accuracy)
        for s, score in result: #letters in one row/column
          
            for letter in s:
                letter_prob[letter] += score
            if (markers_processed%12 == 0):
                trues = '\n\nTrial #' + str(int(markers_processed/12)+1) + ':\t' + str(np.count_nonzero(y_pred[-12:] == y_true[-12:])) + '/12 correct P300 predictions'
                file.write(trues)
                res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
                file.write('\nAccumulated metrics: ')
                file.write(res)
                current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
                if (current_letter.upper() == TRUE_LABELS[len(endresult)]) & (not correct_letter):
                    n_trial = int(markers_processed/12)+1
                    file.write('\n\n~~~~~Character #{} ({}) predicted in {} trials'.format(len(endresult)+1,
                                                                                  current_letter, int(n_trial)))
                    correct_letter = True
#                 if (markers_processed != 180) & (not correct_letter):
#                     if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                          file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                           current_letter, int(markers_processed/12)))
                # Ch_#, Trial_#, isCorrect_ch_pred, correct/12, recall_now, precision_now, 
                #recall, precision, accuracy
                resultsFile.write('\n'+str(len(endresult)+1)+','+str(int(markers_processed/12)+1)+','
                                  +str(np.count_nonzero(y_pred[-12:] == y_true[-12:]))+','+str(correct_letter)+
                                  ','+str(recall)+','+str(precision)+','+str(accuracy))

                if markers_processed == 180: # 12 trials x 15 repetitions = 180
                    endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
                    # Set all probabilities to zero
                    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
                    markers_processed = -1
                    if not correct_letter:
                        file.write('\n\nFailed to predict character #{}'.format(len(endresult)))
    #                         file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
    #                         res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
    #                         file.write(res)
                    n_ch = len(endresult)
                    # 0: character not predicted in trial, 1: character correctly predicted
                    if correct_letter:
                        trial_results = ('0,'*(n_trial-1)+(16-n_trial+1)*'1,')[:-1]
                    else:
                        trial_results = ('0,'*16)[:-1]
                    
                    chResultsFile.write('\n'+str(n_ch)+','+trial_results)
                    correct_letter = False        
                    file.write('\n\nCharacter #'+str(n_ch+1))

            markers_processed += 1

                
#             if (markers_processed%12 == 0) & (markers_processed != 180) & (not correct_letter):
#                 current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
#                 if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                     file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                   current_letter, int(markers_processed/12)))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
#                     correct_letter = True
           
#             elif markers_processed == 180: # 12 trials x 15 repetitions = 180
#                 endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
#                 # Set all probabilities to zero
#                 letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
#                 markers_processed = 0
#                 if not correct_letter:
#                     file.write('\n\nFailed to predict character #{} in 15 trials'.format(len(endresult)))
#                     file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
#                     res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
#                     file.write(res)
                    
#                 correct_letter = False
# #                 current_letter_idx += 1
# #                 print('letter idx', current_letter_idx)
# #                 current_letter = TRUE_LABELS[current_letter_idx].lower()
#             markers_processed += 1
#         print(letter_prob)
#         logger.debug("".join([i[0] for i in sorted(letter_prob.items(), key=lambda x: x[1], reverse=True)]).replace(current_letter, " %s " % current_letter))

        # calculate the current accuracy
        if len(endresult) > 0:
            logger.debug(TRUE_LABELS)
            logger.debug("".join(endresult))
            acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
            print('Character prediction metrics...')
            print("Current accuracy:", acc * 100)
            print('{}/{} characters predicted'.format(len(endresult), len(TRUE_LABELS)))
        if len(endresult) == len(TRUE_LABELS)-1:
            break
        #logger.debug("Result: %s" % result)
        print('time',1000 * (time.time() - t0))

    acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
    print ("Accuracy:", acc * 100)
    file.close()
    resultsFile.close()

    amp.stop()


In [16]:


from __future__ import division

import time

import numpy as np

from libmushu.amplifier import Amplifier


class RReeplayAmp(Amplifier):

    def configure(self, data, marker, channels, fs, realtime=True, blocksize_ms=None, blocksize_samples=None):
        """

        Parameters
        ----------
        data
        marker
        channels
        fs
        realtime
        blocksize_ms : float
            blocksize in milliseconds
        blocksize_samples : int
            blocksize in samples

        Raises
        ------
        TypeError :
            if ``blocksize_ms`` and ``blocksize_s`` are given.

        """
        if [blocksize_ms, blocksize_samples].count(None) != 1:
            raise TypeError("blocksize_ms and blocksize_samples are mutually exclusive.")

        self.data = data
        # slow python
        self.marker = marker
        # fast numpy
        self.marker_ts = np.array([ts for ts, s in marker])
        self.marker_s = np.array([s for ts, s in marker])
        self.channels = channels
        self.fs = fs
        self.realtime = realtime

        if blocksize_ms:
            samples = fs * (blocksize_ms / 1000)
            if not samples.is_integer():
                raise ValueError("Resulting blocksize is not integer, please fix the blocksize_ms.")
            self.samples = samples
        if blocksize_samples:
            self.samples = blocksize_samples

    def start(self):
        self.last_sample_time = time.time()
        self.pos = 0

    def stop(self):
        pass

    def get_data(self):
        """

        Returns
        -------
        chunk, markers: Markers is time in ms since relative to the
        first sample of that block.

        """
        if self.realtime:
            elapsed = time.time() - self.last_sample_time
            blocks = (self.fs * elapsed) // self.samples
            samples = int(blocks * self.samples)
            
        else:
            samples = self.samples
      
        elapsed = samples / self.fs
        self.last_sample_time += elapsed
        # data
        chunk = self.data[self.pos:int(self.pos+samples)]
        #self.data = self.data[samples:]
        # markers

        # slow python version
        #markers = [x for x in self.marker if x[0] < elapsed * 1000]
        #self.marker = [x for x in self.marker if x[0] >= elapsed * 1000]
        #self.marker = [[x[0] - elapsed * 1000, x[1]] for x in self.marker]

        # fast numpy version
        mask = self.marker_ts < (elapsed * 1000) 
        markers = list(zip(self.marker_ts[mask], self.marker_s[mask]))
        self.marker_ts = self.marker_ts[~mask]
        self.marker_s = self.marker_s[~mask]
        self.marker_ts -= elapsed * 1000

        self.pos += samples
        return chunk, markers

    def get_channels(self):
        return self.channels

    def get_sampling_frequency(self):
        return self.fs

    @staticmethod
    def is_available():
        return True


In [17]:
def preprocessing_simple(dat, MRK_DEF, *args, **kwargs):
    """Simple preprocessing that reaches 97% accuracy.
    """
    fs_n = dat.fs / 2
    b, a = proc.signal.butter(5, [10 / fs_n], btype='low')
    dat = proc.filtfilt(dat, b, a)
   
    dat = proc.subsample(dat, 20)
    epo = proc.segment_dat(dat, MRK_DEF, SEG_IVAL)
    fv = proc.create_feature_vectors(epo)
    return fv, epo

In [18]:
subject = 'B'
if subject == 'A':
    TRAIN_DATA = TRAIN_DATA_A
elif subject == 'B':
    TRAIN_DATA = TRAIN_DATA_B
data_m = loadmat(TRAIN_DATA)
target_chars = data_m.get('TargetChar')[0][60:]
TRUE_LABELS = target_chars

In [19]:
TRUE_LABELS

'KOJDWZEUEWWFOEBHXTQTTZUMO'

# 1. Training (off-line)

In [12]:
dat_train = load_bci_TRAINdata(TRAIN_DATA)

In [13]:
fv_train, epo = preprocessing_simple(dat_train, MARKER_DEF_TRAIN, SEG_IVAL)
fv_valid, _ = preprocessing_simple(dat_train, MARKER_DEF_TRAIN, SEG_IVAL)
fv_test, _ = preprocessing_simple(dat_test, MARKER_DEF_TRAIN, SEG_IVAL)

In [14]:
x = fv_train.data #traininig samples
y = fv_train.axes[0] #class labels

In [15]:
scaler = MinMaxScaler()
scaler.fit(x)
X = scaler.transform(x)
X_test = scaler.transform(fv_test.data)

In [87]:
X_train, X_valid, y_train, y_valid = train_test_split(x, y, test_size = 0.3, train_size = 0.7)


In [16]:
clf = SVC(kernel='linear', C=0.1, class_weight='balanced', probability=True)
#CalibratedClassifierCV(base_estimator=LinearSVC(C = 1, class_weight = 'balanced'), cv=2)
clf.fit(X, y)
pred = clf.predict_proba(X_test)

In [26]:
# save classifier
filename = 'Trained Classifiers/'+subject+'/LinearSVM_C-0.1_'+subject+'.pkl'
joblib.dump(clf, filename)

['../Trained Classifiers/A/LinearSVM_C-0.1_A.pkl']

In [17]:
y_test = fv_test.axes[0]
pred_class = clf.predict(X_test)
report = metrics.classification_report(y_test, pred_class)
acc = metrics.accuracy_score(y_test, pred_class)
cm = metrics.confusion_matrix(y_test, pred_class)
tn = cm[0,0] 
tp = cm[1,1]
cm[0,0] = tp
cm[1,1] = tn
print(report)

             precision    recall  f1-score   support

          0       0.90      0.69      0.78      3750
          1       0.28      0.62      0.39       750

avg / total       0.80      0.68      0.71      4500



In [18]:
def predict_character(pred, n_characters, fv_test, labels):
    pred_target = pred
    #unscramble_idx = fv_test.stimulus_code.reshape(100, 15, 12).argsort()
    unscramble_idx = fv_test.stimulus_code.reshape(n_characters, -1, 12).argsort()
    static_idx = np.indices(unscramble_idx.shape)
    #lda_out_prob = pred.reshape(100, 15, 12)
    lda_out_prob = pred.reshape(n_characters, -1, 12)
    lda_out_prob = lda_out_prob[static_idx[0], static_idx[1], unscramble_idx]

    # destil the result of the 15 runs
    lda_out_prob = lda_out_prob.sum(axis=1)
    lda_out_prob = lda_out_prob.argsort()


    cols = lda_out_prob[lda_out_prob <= 5].reshape(n_characters, -1)
    rows = lda_out_prob[lda_out_prob > 5].reshape(n_characters, -1)
    text = ''
    for i in range(n_characters):
        row = rows[i][-1]-6
        col = cols[i][-1]
        letter = MATRIX[row][col]
        text += letter
    print()
    print('Constructed labels: %s' % text.upper())
    print('True labels       : %s' % labels)
    a = np.array(list(text.upper()))
    b = np.array(list(labels))
    accuracy = np.count_nonzero(a == b) / len(a)
    print('Accuracy: %.1f%%' % (accuracy * 100))
    

In [21]:
predict_character(pred[:,1], 25, fv_test, TRUE_LABELS)


Constructed labels: W4AKTLBWXEPOUIKZERZOOTH9C
True labels       : W_EKTLBWXEPOUIKZERYOOTHQI
Accuracy: 80.0%


# 2. Online experiment

In [34]:
C = '0.1'
# load classifier
filename = 'Trained Classifiers/'+subject+'/LinearSVM_C='+C+'_'+subject+'.pkl'
clf = joblib.load(filename)

In [35]:
# load scaler
filename = 'Trained Classifiers/'+subject+'/LinearSVMScaler_'+subject+'.pkl'
scaler = joblib.load(filename)

In [36]:
bbuffer = BlockBuffer(12)
cnt = load_bci_TESTdata(TRAIN_DATA)

In [37]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [38]:
online_experiment(amp, clf, scaler, subject, C)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
DEBUG:__

Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 33.908843994140625
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 34.903526306152344
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6666666666666666
time 35.906076431274414
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.75
time 43.885231018066406
Predicho:  [0] 	Verdadero:  [1] [False]


DEBUG:__main__:Markers processed: 
DEBUG:__main__:5
DEBUG:__main__:Markers processed: 
DEBUG:__main__:6
DEBUG:__main__:Markers processed: 
DEBUG:__main__:7
DEBUG:__main__:Markers processed: 
DEBUG:__main__:8



P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6
time 36.90052032470703
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 46.872854232788086
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.42857142857142855
time 34.90018844604492
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 43.88236999511719
Predicho:  [0] 	Verdadero:  [0] [ True]


DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers processed: 
DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11


...

Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.574792243767313 	precision:  0.3158295281582953 	f1:  0.4076620825147348 	accuracy:  0.7218634686346863
Character prediction metrics...
Current accuracy: 82.6086956521739
23/25 characters predicted
time 57.016849517822266
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.574792243767313 	precision:  0.3155893536121673 	f1:  0.4074619538537064 	accuracy:  0.7216970255937284
Character prediction metrics...
Current accuracy: 82.6086956521739
23/25 characters predicted
time 50.864219665527344
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.574792243767313 	precision:  0.3155893536121673 	f1:  0.4074619538537064 	accuracy:  0.7217611802674043
Character prediction metrics...
Current accuracy: 82.6086956521739
23/25 characters predicted
time 61.83338165283203


DEBUG:__main__:Markers processed: 
DEBUG:__main__:175
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:kojdwveuevwfoebhxvqttvu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:176
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:kojdwveuevwfoebhxvqttvu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:177
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:kojdwveuevwfoebhxvqttvu


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.574792243767313 	precision:  0.3155893536121673 	f1:  0.4074619538537064 	accuracy:  0.7218253053699009
Character prediction metrics...
Current accuracy: 82.6086956521739
23/25 characters predicted
time 62.83307075500488
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.573997233748271 	precision:  0.3155893536121673 	f1:  0.4072620215897939 	accuracy:  0.7216589861751153
Character prediction metrics...
Current accuracy: 82.6086956521739
23/25 characters predicted
time 54.854393005371094
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.573997233748271 	precision:  0.3155893536121673 	f1:  0.4072620215897939 	accuracy:  0.7217231052752822
Character prediction metrics...
Current accuracy: 82.6086956521739
23/25 characters predicted
time 57.84440040588379


DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:kojdwveuevwfoebhxvqttvu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:kojdwveuevwfoebhxvqttvu
DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:KOJDWZEUEWWFOEBHXTQTTZUMO
DEBUG:__main__:kojdwveuevwfoebhxvqttvum


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.573997233748271 	precision:  0.3155893536121673 	f1:  0.4072620215897939 	accuracy:  0.7217871948410871
Character prediction metrics...
Current accuracy: 82.6086956521739
23/25 characters predicted
time 52.85811424255371
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.573997233748271 	precision:  0.3155893536121673 	f1:  0.4072620215897939 	accuracy:  0.7218512548929311
Character prediction metrics...
Current accuracy: 82.6086956521739
23/25 characters predicted
time 56.85019493103027
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.5732044198895028 	precision:  0.3155893536121673 	f1:  0.4070622854340363 	accuracy:  0.7216850828729282
Character prediction metrics...
Current accuracy: 83.33333333333334
24/25 characters predicted
Accuracy: 83.33333333333334


# Gaussian SVM

In [82]:
def online_experiment_gaussian(amp, cfy, scaler, subject, C, gamma):
    amp_fs = amp.get_sampling_frequency()
    amp_channels = amp.get_channels()
    C = str(C)
    file = open('sim_training_GaussianSVM_C='+C+'_g='+gamma+'_'+subject+'.txt', 'w')
    file.write('GaussianSVM C='+C+', g='+gamma+' '+'Online simulation, subject '+subject)
    
    # csv results file
    filename = 'results/'+subject+'/Results_GaussianSVM_C='+C+'_g='+gamma+'_'+subject+'.csv'
    columnNames = 'Character,Trial,Correct/12,isCorrect_ch_pred,recall_acum,precision_acum,accuracy'

    resultsFile = open(filename, 'w')
    resultsFile.write(columnNames)    
    
    chfilename = 'results/'+subject+'/CharacterResults_GaussianSVM_C='+C+'_g='+gamma+'_'+subject+'.csv'
    chcolumnNames = 'Character,Trial 1,Trial 2,Trial 3,Trial 4,Trial 5, Trial 6,\
    Trial 7,Trial 8,Trial 9,Trial 10,Trial 11,Trial 12,Trial 13,Trial 14,Trial 15,Trial 16'
    chResultsFile = open(chfilename, 'w')
    chResultsFile.write(chcolumnNames)     

    #buf = BlockBuffer(4)
    rb = RingBuffer(5000)

    fn = amp_fs / 2
    b_low, a_low = proc.signal.butter(5, [10 / fn], btype='low')
#     b_high, a_high = proc.signal.butter(5, [.4 / fn], btype='high')

    zi_low = proc.lfilter_zi(b_low, a_low, len(amp_channels))
#     zi_high = proc.lfilter_zi(b_high, a_high, len(amp_channels))

    amp.start()
    markers_processed = 0
#     current_letter_idx = 0
#     current_letter = TRUE_LABELS[current_letter_idx].lower()

    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
    endresult = []
    file.write('\nCharacter #'+str(len(endresult)+1))

   # t0 = time.time()
    #data, markers = amp.get_data()
    
    y_true = np.array([])
    y_pred = np.array([])
    
    correct_letter = False #boolean to know if the letter has already been predicted
    
    while True:
        t0 = time.time()

        # get fresh data from the amp
        data, markers = amp.get_data()
        if len(data) == 0:
            continue

        # we should rather wait for a specific end-of-experiment marker
        if len(data) == 0:
            break

        # convert to cnt
        cnt = io.convert_mushu_data(data, markers, amp_fs, amp_channels)
        
        ## enter the block buffer
        #buf.append(cnt)
        #cnt = buf.get()
        #if not cnt:
        #    continue

        # low-pass and subsample
        cnt, zi_low = proc.lfilter(cnt, b_low, a_low, zi=zi_low)
#         cnt, zi_high = proc.lfilter(cnt, b_high, a_high, zi=zi_high)

        cnt = proc.subsample(cnt, 20)

        newsamples = cnt.data.shape[0]

        # enter the ringbuffer
        rb.append(cnt)
        cnt = rb.get()

        # segment
        epo = proc.segment_dat(cnt, MARKER_DEF_TEST, SEG_IVAL, newsamples=newsamples)
        epo_train = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL, newsamples=newsamples)
        if not epo: # If not enough data for 800 ms
            continue

        fv = proc.create_feature_vectors(epo)
        fv_train = proc.create_feature_vectors(epo_train)
        
        logger.debug('Markers processed: ')
        logger.debug(markers_processed)
        
        
        clf_out = cfy.predict_proba(scaler.transform(fv.data))[:,1] #Estimate probabilities
        y_true = np.append(y_true, fv_train.axes[0])
        
        y_pred_now = cfy.predict(scaler.transform(fv.data))  #Predict classes
        y_pred = np.append(y_pred, y_pred_now)
        
        y_correct = y_pred_now == fv_train.axes[0]
        print('Predicho: ', fv_train.axes[0],'\tVerdadero: ', y_pred_now, y_correct )

#         clf_out = proc.lda_apply(fv, cfy)
        markers = [fv.class_names[cls_idx] for cls_idx in fv.axes[0]]
        result = zip(markers, clf_out)
        
        report = metrics.classification_report(y_true, y_pred)
        recall = metrics.recall_score(y_true, y_pred)
        precision = metrics.precision_score(y_true, y_pred)
        accuracy = metrics.accuracy_score(y_true, y_pred)
        f1 = metrics.f1_score(y_true, y_pred)
        print('\nP300 classification metrics...')
        print('recall: ', recall, '\tprecision: ', precision, '\tf1: ', f1, '\taccuracy: ', accuracy)
        for s, score in result: #letters in one row/column
          
            for letter in s:
                letter_prob[letter] += score
            if (markers_processed%12 == 0):
                trues = '\n\nTrial #' + str(int(markers_processed/12)+1) + ':\t' + str(np.count_nonzero(y_pred[-12:] == y_true[-12:])) + '/12 correct P300 predictions'
                file.write(trues)
                res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
                file.write('\nAccumulated metrics: ')
                file.write(res)
                current_letter = sorted(letter_prob.items(), key=lambda x: x[1])[-1][0]
                if (current_letter.upper() == TRUE_LABELS[len(endresult)]) & (not correct_letter):
                    n_trial = int(markers_processed/12)+1
                    file.write('\n\n~~~~~Character #{} ({}) predicted in {} trials'.format(len(endresult)+1,
                                                                                  current_letter, int(n_trial)))
                    correct_letter = True
#                 if (markers_processed != 180) & (not correct_letter):
#                     if(current_letter.upper() == TRUE_LABELS[len(endresult)]):
#                          file.write('\n\nCharacter #{} ({}) predicted in {} trials'.format(len(endresult),
#                                                                                           current_letter, int(markers_processed/12)))
                # Ch_#, Trial_#, isCorrect_ch_pred, correct/12, recall_now, precision_now, 
                #recall, precision, accuracy
                resultsFile.write('\n'+str(len(endresult)+1)+','+str(int(markers_processed/12)+1)+','
                                  +str(np.count_nonzero(y_pred[-12:] == y_true[-12:]))+','+str(correct_letter)+
                                  ','+str(recall)+','+str(precision)+','+str(accuracy))

                if markers_processed == 180: # 12 trials x 15 repetitions = 180
                    endresult.append(sorted(letter_prob.items(), key=lambda x: x[1])[-1][0])
                    # Set all probabilities to zero
                    letter_prob = {i : 0 for i in 'abcdefghijklmnopqrstuvwxyz123456789_'}
                    markers_processed = -1
                    if not correct_letter:
                        file.write('\n\nFailed to predict character #{}'.format(len(endresult)))
    #                         file.write('\nPredicted {} instead of {}.'.format(current_letter.upper(), TRUE_LABELS[len(endresult)]))
    #                         res = '\nrecall: ' + str(recall) + '\tprecision: ' + str(precision) + '\tf1: ' + str(f1) + '\taccuracy: ' + str(accuracy)
    #                         file.write(res)
                    n_ch = len(endresult)
                    # 0: character not predicted in trial, 1: character correctly predicted
                    if correct_letter:
                        trial_results = ('0,'*(n_trial-1)+(16-n_trial+1)*'1,')[:-1]
                    else:
                        trial_results = ('0,'*16)[:-1]
                    
                    chResultsFile.write('\n'+str(n_ch)+','+trial_results)
                    correct_letter = False        
                    file.write('\n\nCharacter #'+str(n_ch+1))

            markers_processed += 1
        # calculate the current accuracy
        if len(endresult) > 0:
            logger.debug(TRUE_LABELS)
            logger.debug("".join(endresult))
            acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
            print('Character prediction metrics...')
            print("Current accuracy:", acc * 100)
            print('{}/{} characters predicted'.format(len(endresult), len(TRUE_LABELS)))
        if len(endresult) == len(TRUE_LABELS)-1:
            break
        #logger.debug("Result: %s" % result)
        print('time',1000 * (time.time() - t0))

    acc = np.count_nonzero(np.array(endresult) == np.array(list(TRUE_LABELS.lower()[:len(endresult)]))) / len(endresult)
    print ("Accuracy:", acc * 100)
    file.close()
    resultsFile.close()

    amp.stop()


In [37]:
subject = 'A'
if subject == 'A':
    TRAIN_DATA = TRAIN_DATA_A
elif subject == 'B':
    TRAIN_DATA = TRAIN_DATA_B
data_m = loadmat(TRAIN_DATA)
target_chars = data_m.get('TargetChar')[0][60:]
TRUE_LABELS = target_chars

In [38]:
C = '1000'
gamma = '0.001'
# load classifier
filename = 'Trained Classifiers/'+subject+'/GaussianSVM_C='+C+'-g='+gamma+'_'+subject+'.pkl'
clf = joblib.load(filename)

### Online experiment

In [39]:
# load scaler
filename = 'Trained Classifiers/'+subject+'/SVMScaler_'+subject+'.pkl'
scaler = joblib.load(filename)

In [40]:
bbuffer = BlockBuffer(12)
cnt = load_bci_TESTdata(TRAIN_DATA)

In [41]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [42]:
online_experiment_gaussian(amp, clf, scaler, subject, C, gamma)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples.
  'recall', 'true', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 due to no true samples.
  'recall', 'true', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1137: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no true samples.
  'recall', 'true', average, warn_for)
DEBUG:__main__:Markers processed: 
DE

Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 29.91461753845215
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.0
time 28.921127319335938
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.3333333333333333
time 26.928186416625977
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 28.922319412231445
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.3333333333333333 	f1:  0.5 	accuracy:  0.6
time 29.920578002929688


DEBUG:__main__:Markers processed: 
DEBUG:__main__:6
DEBUG:__main__:Markers processed: 
DEBUG:__main__:7
DEBUG:__main__:Markers processed: 
DEBUG:__main__:8
DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers processed: 


Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  1.0 	precision:  0.25 	f1:  0.4 	accuracy:  0.5
time 45.870065689086914
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  1.0 	precision:  0.25 	f1:  0.4 	accuracy:  0.5714285714285714
time 28.922319412231445
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.5 	precision:  0.25 	f1:  0.3333333333333333 	accuracy:  0.5
time 31.914949417114258
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5 	precision:  0.25 	f1:  0.3333333333333333 	accuracy:  0.5555555555555556
time 33.91098976135254
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5 	precision:  0.25 	f1:  0.3333333333333333 	accuracy:  0.6
time 32.91058540344238


DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13
DEBUG:__main__:Markers processed: 
DEBUG:__main__:14


...


P300 classification metrics...
recall:  0.5449515905947441 	precision:  0.2920681986656783 	f1:  0.3803088803088803 	accuracy:  0.7040110650069157
Character prediction metrics...
Current accuracy: 52.17391304347826
23/25 characters predicted
time 52.85906791687012
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.5441988950276243 	precision:  0.2920681986656783 	f1:  0.3801254220935842 	accuracy:  0.7038488130905739
Character prediction metrics...
Current accuracy: 52.17391304347826
23/25 characters predicted
time 49.867868423461914
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.5441988950276243 	precision:  0.29185185185185186 	f1:  0.3799421407907425 	accuracy:  0.7036866359447005
Character prediction metrics...
Current accuracy: 52.17391304347826
23/25 characters predicted
time 55.84859848022461


DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:w_aktlbxfkpouiwzcr4uuzk
DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:w_aktlbxfkpouiwzcr4uuzk
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5441988950276243 	precision:  0.29185185185185186 	f1:  0.3799421407907425 	accuracy:  0.7037548951854411
Character prediction metrics...
Current accuracy: 52.17391304347826
23/25 characters predicted
time 73.34113121032715
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.5441988950276243 	precision:  0.29163582531458176 	f1:  0.37975903614457834 	accuracy:  0.7035928143712575
Character prediction metrics...
Current accuracy: 52.17391304347826
23/25 characters predicted
time 67.82031059265137
Predicho:  [0] 	Verdadero:  [0] [ True]


DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:w_aktlbxfkpouiwzcr4uuzk
DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:W_EKTLBWXEPOUIKZERYOOTHQI
DEBUG:__main__:w_aktlbxfkpouiwzcr4uuzk9



P300 classification metrics...
recall:  0.5441988950276243 	precision:  0.29163582531458176 	f1:  0.37975903614457834 	accuracy:  0.7036610637807967
Character prediction metrics...
Current accuracy: 52.17391304347826
23/25 characters predicted
time 52.85835266113281
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5441988950276243 	precision:  0.29163582531458176 	f1:  0.37975903614457834 	accuracy:  0.7037292817679558
Character prediction metrics...
Current accuracy: 50.0
24/25 characters predicted
Accuracy: 50.0


## Sujeto C

In [44]:
def load_bci_TRAINdata2(filenames):

    STIMULUS_CODE = {
            0 : "blankMatrix",
            # cols from left to right
            1 : "agmsy5",
            2 : "bhntz6",
            3 : "ciou17",
            4 : "djpv28",
            5 : "ekqw39",
            6 : "flrx4_",
            # rows from top to bottom
            7 : "abcdef",
            8 : "ghijkl",
            9 : "mnopqr",
            10: "stuvwx",
            11: "yz1234",
            12: "56789_"
            }


    # # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filenames[0]), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2

    data_mat0 = loadmat(filenames[0])    
    data = data_mat0['signal']
    flashing = data_mat0['Flashing'].reshape(-1)
    stimulus_code = data_mat0['StimulusCode'].reshape(-1)
    stimulus_type = data_mat0.get('StimulusType', np.array([])).reshape(-1)
    sequence_phase = data_mat0['PhaseInSequence']

    #print(data.shape, flashing.shape, stimulus_code.shape, stimulus_type.shape)

    for i, filename in enumerate(filenames):
        if i == 0:
            continue
        # load the matlab data
        data_mat = loadmat(filename)
        # The signal is recorded with 64 channels, bandpass filtered
        # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
        # Samples x Channels
        data_temp = data_mat['signal']
        data = np.append(data, data_temp).reshape(-1, 64)
        data = data.astype('double')

        # For each sample: 1 if a row/colum was flashed, 0 otherwise
        flashing = np.append(flashing, data_mat['Flashing'].reshape(-1))
        #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
        ##Creates an array where only the initial intensifications of each series appear
        tmp = []
        for i, _ in enumerate(flashing):
            if i == 0:
                tmp.append(flashing[i])
                continue
            if flashing[i] == flashing[i-1] == 1:
                tmp.append(0)
                continue
            tmp.append(flashing[i])
        flashing = np.array(tmp)

        # For each sample: 0 when no row/colum was intensified,
        # 1..6 for intensified columns, 7..12 for intensified rows
        stimulus_code = np.append(stimulus_code, data_mat['StimulusCode'].reshape(-1))

        # 0 if no row/col was intensified or the intensified did not contain
        # the target character, 1 otherwise
        stimulus_type = np.append(stimulus_type, data_mat.get('StimulusType', np.array([]).reshape(-1)))
        sequence_phase = np.append(sequence_phase, data_mat['PhaseInSequence'])
  
    # Erase last 12 samples in order to reshape to (42,-1)
    flashing = flashing.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    stimulus_code = stimulus_code.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    stimulus_type = stimulus_type.reshape(-1)[:-12].reshape(42,-1)[:30,:].reshape(-1)
    
    # Erase last 768 samples in order to reshape to (42,-1,64 )
    data = data.reshape(-1)[:-768].reshape(42,-1,64)
    data = data[:30,:,:] # Get first 20 characters for training data 
    data = data.reshape(-1, 64)
    fs = 240
    stimulus_code = stimulus_code[flashing == 1]
 
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
   # dat.sequence_phase = sequence_phase
    return dat


In [45]:
def load_bci_TESTdata2(filenames):

    STIMULUS_CODE = {
            0 : "blankMatrix",
            # cols from left to right
            1 : "agmsy5",
            2 : "bhntz6",
            3 : "ciou17",
            4 : "djpv28",
            5 : "ekqw39",
            6 : "flrx4_",
            # rows from top to bottom
            7 : "abcdef",
            8 : "ghijkl",
            9 : "mnopqr",
            10: "stuvwx",
            11: "yz1234",
            12: "56789_"
            }


    # # load the channel names (the same for all datasets
    eloc_file = path.sep.join([path.dirname(filenames[0]), 'eloc64.txt'])
    with open(eloc_file) as fh:
        data = fh.read()
    channels = []
    for line in data.splitlines():
        if line:
            chan = line.split()[-1]
            chan = chan.replace('.', '')
            channels.append(chan)
    # # fix the channel names, some letters have the wrong capitalization
    for i, s in enumerate(channels):
        s2 = s.upper()
        s2 = s2.replace('Z', 'z')
        s2 = s2.replace('FP', 'Fp')
        channels[i] = s2

    data_mat0 = loadmat(filenames[0])    
    data = data_mat0['signal']
    flashing = data_mat0['Flashing'].reshape(-1)
    stimulus_code = data_mat0['StimulusCode'].reshape(-1)
    stimulus_type = data_mat0.get('StimulusType', np.array([])).reshape(-1)
    sequence_phase = data_mat0['PhaseInSequence']

    #print(data.shape, flashing.shape, stimulus_code.shape, stimulus_type.shape)

    for i, filename in enumerate(filenames):
        if i == 0:
            continue
        # load the matlab data
        data_mat = loadmat(filename)
        # The signal is recorded with 64 channels, bandpass filtered
        # 0.1-60Hz and digitized at 240Hz. The format is Character Epoch x
        # Samples x Channels
        data_temp = data_mat['signal']
        data = np.append(data, data_temp).reshape(-1, 64)
        data = data.astype('double')

        # For each sample: 1 if a row/colum was flashed, 0 otherwise
        flashing = np.append(flashing, data_mat['Flashing'].reshape(-1))
        #flashing = np.flatnonzero((np.diff(a) == 1)) + 1
        ##Creates an array where only the initial intensifications of each series appear
        tmp = []
        for i, _ in enumerate(flashing):
            if i == 0:
                tmp.append(flashing[i])
                continue
            if flashing[i] == flashing[i-1] == 1:
                tmp.append(0)
                continue
            tmp.append(flashing[i])
        flashing = np.array(tmp)

        # For each sample: 0 when no row/colum was intensified,
        # 1..6 for intensified columns, 7..12 for intensified rows
        stimulus_code = np.append(stimulus_code, data_mat['StimulusCode'].reshape(-1))

        # 0 if no row/col was intensified or the intensified did not contain
        # the target character, 1 otherwise
        stimulus_type = np.append(stimulus_type, data_mat.get('StimulusType', np.array([]).reshape(-1)))
        sequence_phase = np.append(sequence_phase, data_mat['PhaseInSequence'])
  
    # Erase last 12 samples in order to reshape to (42,-1)
    flashing = flashing.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    stimulus_code = stimulus_code.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    stimulus_type = stimulus_type.reshape(-1)[:-12].reshape(42,-1)[30:,:].reshape(-1)
    
    # Erase last 768 samples in order to reshape to (42,-1,64 )
    data = data.reshape(-1)[:-768].reshape(42,-1,64)
    data = data[30:,:,:] # Get first 20 characters for training data 
    data = data.reshape(-1, 64)
    fs = 240
    stimulus_code = stimulus_code[flashing == 1]
 
    timeaxis = np.linspace(0, data.shape[0] / fs * 1000, data.shape[0], endpoint=False)
    dat = Data(data=data, axes=[timeaxis, channels], names=['time', 'channel'], units=['ms', '#'])
    dat.fs = fs
    # preparing the markers
    target_mask = np.logical_and((flashing == 1), (stimulus_type == 1)) if len(stimulus_type) > 0 else []
    nontarget_mask = np.logical_and((flashing == 1), (stimulus_type == 0)) if len(stimulus_type) > 0 else []
    flashing = (flashing == 1)
    flashing = [[i, 'flashing'] for i in timeaxis[flashing]]
    targets = [[i, 'target'] for i in timeaxis[target_mask]]
    nontargets = [[i, 'nontarget'] for i in timeaxis[nontarget_mask]]
    dat.stimulus_code = stimulus_code[:]
    stim = []
    for i,_ in enumerate(flashing):
        stim.append([flashing[i][0], STIMULUS_CODE[stimulus_code[i]]])
    stimulus_code = stim
    markers = flashing[:]
    markers.extend(targets)
    markers.extend(nontargets)
    markers.extend(stimulus_code)
    markers.sort()
    dat.markers = markers[:]
   # dat.sequence_phase = sequence_phase
    return dat


In [46]:
labels = 'CATDOGFISHWATERBOWLHATHATGLOVESHOESFISHRAT'
path_ = '../BCI_Comp_II_2003/data/'
datafiles = [join(path_,f) for f in listdir(path_) if isfile(join(path_, f))]
training_set = [f for i,f in enumerate(datafiles) if '12' not in f and 'eloc64' not in f]
testing_set = [f for i,f in enumerate(datafiles) if '12' in f and 'eloc64' not in f]

In [47]:
# load the training set
dat_train = load_bci_TRAINdata2(training_set)


In [48]:
TRUE_LABELS = labels[30:]
TRUE_LABELS

'SHOESFISHRAT'

### Training

In [71]:
def train_d2(dat, kernel, C, gamma=None):
    cnt = dat

    fs_n = cnt.fs / 2

    b, a = proc.signal.butter(5, [10 / fs_n], btype='low')
    cnt = proc.lfilter(cnt, b, a)

#     b, a = proc.signal.butter(5, [.4 / fs_n], btype='high')
#     cnt = proc.lfilter(cnt, b, a)

    cnt = proc.subsample(cnt, 20)

    epo = proc.segment_dat(cnt, MARKER_DEF_TRAIN, SEG_IVAL)

    #from wyrm import plot
    #plot.plot_spatio_temporal_r2_values(proc.sort_channels(epo))
    #print JUMPING_MEANS_IVALS
    #plot.plt.show()

    fv = proc.create_feature_vectors(epo)
    scaler = MinMaxScaler()
    X = scaler.fit_transform(fv.data)
    y = fv.axes[0]
    if kernel == 'linear':
        clf = SVC(kernel = kernel, C=C, probability=True, class_weight='balanced')
    elif kernel == 'rbf':
        clf = SVC(kernel = kernel, C=C, gamma=gamma, probability=True, class_weight='balanced')
    clf.fit(X,y)
    return clf, scaler

In [72]:
clf, scaler = train_d2(dat_train, kernel='rbf', C=1000, gamma=0.1)

In [87]:
# save scaler
filename = 'Trained Classifiers/'+subject+'/SVMScaler_'+subject+'.pkl'
# joblib.dump(scaler, filename)

In [88]:
scaler = joblib.load(filename)

In [89]:
subject = 'C'
filename = 'Trained Classifiers/'+subject+'/LinearSVM_C=0.1_'+subject+'.pkl'

In [75]:
joblib.dump(clf, filename)

['Trained Classifiers/C/GaussianSVM_C=1000-g=0.1_C.pkl']

In [90]:
clf = joblib.load(filename)

### Online experiment

In [91]:
bbuffer = BlockBuffer(12)
dat_test = load_bci_TESTdata2(training_set)
cnt = dat_test

In [92]:
amp = RReeplayAmp()
amp.configure(data=cnt.data, marker=cnt.markers, channels=cnt.axes[-1], fs=cnt.fs,
              realtime=False, blocksize_samples=12)

In [94]:
online_experiment(amp, clf, scaler, subject, C)

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 

Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 15.969276428222656
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 17.95196533203125
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6666666666666666
time 19.945383071899414
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 18.94974708557129
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6
time 16.954421997070312
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6666666666666666
time 17.90475845336914
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification 

DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers processed: 
DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13
DEBUG:__main__:Markers processed: 
DEBUG:__main__:14



P300 classification metrics...
recall:  0.5 	precision:  0.5 	f1:  0.5 	accuracy:  0.7777777777777778
time 18.94998550415039
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.5 	precision:  0.5 	f1:  0.5 	accuracy:  0.8
time 16.95418357849121
Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.6666666666666666 	precision:  0.6666666666666666 	f1:  0.6666666666666666 	accuracy:  0.8181818181818182
time 17.95220375061035
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.6666666666666666 	precision:  0.6666666666666666 	f1:  0.6666666666666666 	accuracy:  0.8333333333333334
time 19.94490623474121
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.6666666666666666 	precision:  0.6666666666666666 	f1:  0.6666666666666666 	accuracy:  0.8461538461538461
time 20.943880081176758
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.666666

DEBUG:__main__:Markers processed: 
DEBUG:__main__:15
DEBUG:__main__:Markers processed: 
DEBUG:__main__:16
DEBUG:__main__:Markers processed: 
DEBUG:__main__:17
DEBUG:__main__:Markers processed: 
DEBUG:__main__:18
DEBUG:__main__:Markers processed: 
DEBUG:__main__:19


...

Predicho:  [1] 	Verdadero:  [1] [ True]

P300 classification metrics...
recall:  0.7734138972809668 	precision:  0.41830065359477125 	f1:  0.542948038176034 	accuracy:  0.78199291856348
Character prediction metrics...
Current accuracy: 70.0
10/12 characters predicted
time 22.938966751098633
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7734138972809668 	precision:  0.41830065359477125 	f1:  0.542948038176034 	accuracy:  0.782103134479272
Character prediction metrics...
Current accuracy: 70.0
10/12 characters predicted
time 21.941423416137695
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.7710843373493976 	precision:  0.41830065359477125 	f1:  0.5423728813559322 	accuracy:  0.7817079332996463
Character prediction metrics...
Current accuracy: 70.0
10/12 characters predicted
time 21.939992904663086
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7710843373493976 	precision:  0.41830

DEBUG:__main__:Markers processed: 
DEBUG:__main__:172
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoeyfgsnr
DEBUG:__main__:Markers processed: 
DEBUG:__main__:173
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoeyfgsnr
DEBUG:__main__:Markers processed: 
DEBUG:__main__:174
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoeyfgsnr
DEBUG:__main__:Markers processed: 
DEBUG:__main__:175
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoeyfgsnr
DEBUG:__main__:Markers processed: 
DEBUG:__main__:176
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoeyfgsnr
DEBUG:__main__:Markers processed: 
DEBUG:__main__:177
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoeyfgsnr


Character prediction metrics...
Current accuracy: 70.0
10/12 characters predicted
time 21.941661834716797
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7710843373493976 	precision:  0.41830065359477125 	f1:  0.5423728813559322 	accuracy:  0.7821482602118003
Character prediction metrics...
Current accuracy: 70.0
10/12 characters predicted
time 20.946502685546875
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7710843373493976 	precision:  0.41830065359477125 	f1:  0.5423728813559322 	accuracy:  0.782258064516129
Character prediction metrics...
Current accuracy: 70.0
10/12 characters predicted
time 21.943330764770508
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.7710843373493976 	precision:  0.4176182707993475 	f1:  0.5417989417989418 	accuracy:  0.7818639798488665
Character prediction metrics...
Current accuracy: 70.0
10/12 characters predicted
time 21.9419002532959
Predicho:  [0

DEBUG:__main__:Markers processed: 
DEBUG:__main__:178
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoeyfgsnr
DEBUG:__main__:Markers processed: 
DEBUG:__main__:179
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoeyfgsnr
DEBUG:__main__:Markers processed: 
DEBUG:__main__:180
DEBUG:__main__:SHOESFISHRAT
DEBUG:__main__:shoeyfgsnra


Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.7710843373493976 	precision:  0.416260162601626 	f1:  0.5406546990496304 	accuracy:  0.7812971342383107
Character prediction metrics...
Current accuracy: 70.0
10/12 characters predicted
time 21.942853927612305
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7710843373493976 	precision:  0.416260162601626 	f1:  0.5406546990496304 	accuracy:  0.7814070351758794
Character prediction metrics...
Current accuracy: 70.0
10/12 characters predicted
time 19.946813583374023
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.7710843373493976 	precision:  0.416260162601626 	f1:  0.5406546990496304 	accuracy:  0.7815168257157208
Character prediction metrics...
Current accuracy: 72.72727272727273
11/12 characters predicted
Accuracy: 72.72727272727273


## Gaussian SVM

In [102]:
clf, scaler = train_d2(dat_train, kernel='rbf', C=1000, gamma=0.1)

In [103]:
subject = 'C'
filename = 'Trained Classifiers/'+subject+'/GaussianSVM_C=1000-g=0.1_'+subject+'.pkl'

In [104]:
joblib.dump(clf, filename)
# clf = joblib.load(filename)

['Trained Classifiers/C/GaussianSVM_C=1000-g=0.1_C.pkl']

In [105]:
online_experiment_gaussian(amp, clf, scaler, subject, C='1000', gamma='0.1')

DEBUG:__main__:Markers processed: 
DEBUG:__main__:0
DEBUG:__main__:Markers processed: 
DEBUG:__main__:1
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
C:\Users\aleja\Anaconda3\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 due to no predicted samples.
  'precision', 'predicted', average, warn_for)
DEBUG:__main__:Markers processed: 
DEBUG:__main__:2
DEBUG:__main__:Markers processed: 
DEBUG:__main__:3
DEBUG:__main__:Markers processed: 
DEBUG:__main__:4
DEBUG:__main__:Markers processed: 

Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  1.0
time 14.961957931518555
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.5
time 16.955852508544922
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.6666666666666666
time 15.955924987792969
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.75
time 16.956329345703125
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.8
time 15.956878662109375
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.8333333333333334
time 16.954660415649414
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classificat

DEBUG:__main__:Markers processed: 
DEBUG:__main__:9
DEBUG:__main__:Markers processed: 
DEBUG:__main__:10
DEBUG:__main__:Markers processed: 
DEBUG:__main__:11
DEBUG:__main__:Markers processed: 
DEBUG:__main__:12
DEBUG:__main__:Markers processed: 
DEBUG:__main__:13
DEBUG:__main__:Markers processed: 
DEBUG:__main__:14


[0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.8888888888888888
time 17.945051193237305
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.9
time 14.959573745727539
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.9090909090909091
time 15.957117080688477
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.9166666666666666
time 16.954898834228516
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.9230769230769231
time 15.956878662109375
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.0 	precision:  0.0 	f1:  0.0 	accuracy:  0.9285714285714286
time 16.95561408996582
Predicho:  [0] 	Verdadero:  [0] [ True]

P

DEBUG:__main__:Markers processed: 
DEBUG:__main__:15
DEBUG:__main__:Markers processed: 
DEBUG:__main__:16
DEBUG:__main__:Markers processed: 
DEBUG:__main__:17
DEBUG:__main__:Markers processed: 
DEBUG:__main__:18
DEBUG:__main__:Markers processed: 
DEBUG:__main__:19
DEBUG:__main__:Markers processed: 
DEBUG:__main__:20
DEBUG:__main__:Markers processed: 
DEBUG:__main__:21


...

DEBUG:__main__:Markers processed: 
DEBUG:__main__:112
DEBUG:__main__:Markers processed: 
DEBUG:__main__:113
DEBUG:__main__:Markers processed: 
DEBUG:__main__:114
DEBUG:__main__:Markers processed: 
DEBUG:__main__:115
DEBUG:__main__:Markers processed: 
DEBUG:__main__:116



P300 classification metrics...
recall:  0.16666666666666666 	precision:  0.3 	f1:  0.21428571428571427 	accuracy:  0.8035714285714286
time 17.953872680664062
Predicho:  [0] 	Verdadero:  [1] [False]

P300 classification metrics...
recall:  0.16666666666666666 	precision:  0.2727272727272727 	f1:  0.20689655172413793 	accuracy:  0.7964601769911505
time 16.953468322753906
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.16666666666666666 	precision:  0.2727272727272727 	f1:  0.20689655172413793 	accuracy:  0.7982456140350878
time 25.93088150024414
Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.16666666666666666 	precision:  0.2727272727272727 	f1:  0.20689655172413793 	accuracy:  0.8
time 18.94831657409668
Predicho:  [1] 	Verdadero:  [0] [False]

P300 classification metrics...
recall:  0.15789473684210525 	precision:  0.2727272727272727 	f1:  0.19999999999999998 	accuracy:  0.7931034482758621
time 19.94800567626953
Pre

DEBUG:__main__:Markers processed: 
DEBUG:__main__:117


Predicho:  [0] 	Verdadero:  [0] [ True]

P300 classification metrics...
recall:  0.15789473684210525 	precision:  0.2727272727272727 	f1:  0.19999999999999998 	accuracy:  0.7966101694915254
time 17.95172691345215


KeyboardInterrupt: 